In [19]:
from utils import CustomDataset, transform, Convert_ONNX
from torch.utils.data import Dataset, DataLoader
from utils import CustomDataset, TestingDataset, transform
from tqdm import tqdm
import torch
import numpy as np
from resnet_model_mask import  ResidualBlock, ResNet
import torch
import torch.nn as nn
import torch.optim as optim
from tqdm import tqdm 
import torch.nn.functional as F
from torch.optim.lr_scheduler import ReduceLROnPlateau
import pickle

torch.manual_seed(1)
# torch.manual_seed(42)


device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
num_gpus = torch.cuda.device_count()
print(num_gpus)

test_data_dir = '/mnt/buf1/pma/frbnn/test_ready'
test_dataset = TestingDataset(test_data_dir, transform=transform)

num_classes = 2
testloader = DataLoader(test_dataset, batch_size=420, shuffle=True, num_workers=32)

model = ResNet(24, ResidualBlock, [3, 4, 6, 3], num_classes=num_classes).to(device)
model = nn.DataParallel(model)
model = model.to(device)
params = sum(p.numel() for p in model.parameters())
print("num params ",params)

model_1 = 'models_mask/model-43-99.235_42.pt'
# model_1 ='models/model-47-99.125.pt'
model.load_state_dict(torch.load(model_1, weights_only=True))
model = model.eval()

# eval
val_loss = 0.0
correct_valid = 0
total = 0
results = {'output': [],'pred': [], 'true':[], 'freq':[], 'snr':[], 'dm':[], 'boxcar':[]}
model.eval()
with torch.no_grad():
    for images, labels in tqdm(testloader):
        inputs, labels = images.to(device), labels
        outputs = model(inputs, return_mask = True)
        _, predicted = torch.max(outputs, 1)
        results['output'].extend(outputs.cpu().numpy().tolist())
        results['pred'].extend(predicted.cpu().numpy().tolist())
        results['true'].extend(labels[0].cpu().numpy().tolist())
        results['freq'].extend(labels[2].cpu().numpy().tolist())
        results['dm'].extend(labels[1].cpu().numpy().tolist())
        results['snr'].extend(labels[3].cpu().numpy().tolist())
        results['boxcar'].extend(labels[4].cpu().numpy().tolist())
        total += labels[0].size(0)
        correct_valid += (predicted.cpu() == labels[0].cpu()).sum().item()
    
# Calculate training accuracy after each epoch
val_accuracy = correct_valid / total * 100.0
print("===========================")
print('accuracy: ',  val_accuracy)
print("===========================")

import pickle

# Pickle the dictionary to a file
with open('models_mask/test_42.pkl', 'wb') as f:
    pickle.dump(results, f)

from sklearn.metrics import precision_score, recall_score, f1_score

# Example binary labels
true = results['true']  # ground truth
pred = results['pred']  # predicted

# Compute metrics
precision = precision_score(true, pred)
recall = recall_score(true, pred)
f1 = f1_score(true, pred)
# Get confusion matrix: TN, FP, FN, TP
tn, fp, fn, tp = confusion_matrix(true, pred).ravel()

# Compute FPR
fpr = fp / (fp + tn)

print(f"False Positive Rate: {fpr:.3f}")

print(f"Precision: {precision:.3f}")
print(f"Recall: {recall:.3f}")
print(f"F1 Score: {f1:.3f}")


2
num params encoder  50840
num params  21496282


  0%|                                                    | 0/48 [00:00<?, ?it/s]/home/pma/.conda/envs/frbnn/lib/python3.11/site-packages/torch/nn/parallel/parallel_apply.py:79: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.device(device), torch.cuda.stream(stream), autocast(enabled=autocast_enabled):
100%|███████████████████████████████████████████| 48/48 [00:44<00:00,  1.09it/s]

accuracy:  99.125
False Positive Rate: 0.008
Precision: 0.992
Recall: 0.991
F1 Score: 0.991


In [20]:
from utils import CustomDataset, transform, Convert_ONNX
from torch.utils.data import Dataset, DataLoader
from utils import CustomDataset, TestingDataset, transform
from tqdm import tqdm
import torch
import numpy as np
from resnet_model_mask import  ResidualBlock, ResNet
import torch
import torch.nn as nn
import torch.optim as optim
from tqdm import tqdm 
import torch.nn.functional as F
from torch.optim.lr_scheduler import ReduceLROnPlateau
import pickle

torch.manual_seed(1)


device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
num_gpus = torch.cuda.device_count()
print(num_gpus)

test_data_dir = '/mnt/buf1/pma/frbnn/test_ready'
test_dataset = TestingDataset(test_data_dir, transform=transform)

num_classes = 2
testloader = DataLoader(test_dataset, batch_size=420, shuffle=True, num_workers=32)

model = ResNet(24, ResidualBlock, [3, 4, 6, 3], num_classes=num_classes).to(device)
model = nn.DataParallel(model)
model = model.to(device)
params = sum(p.numel() for p in model.parameters())
print("num params ",params)


model_1 = 'models_mask/model-36-99.11999999999999_1.pt'
# model_1 ='models/model-47-99.125.pt'
model.load_state_dict(torch.load(model_1, weights_only=True))
model = model.eval()

# eval
val_loss = 0.0
correct_valid = 0
total = 0
results = {'output': [],'pred': [], 'true':[], 'freq':[], 'snr':[], 'dm':[], 'boxcar':[]}
model.eval()
with torch.no_grad():
    for images, labels in tqdm(testloader):
        inputs, labels = images.to(device), labels
        outputs = model(inputs, return_mask = True)
        _, predicted = torch.max(outputs, 1)
        results['output'].extend(outputs.cpu().numpy().tolist())
        results['pred'].extend(predicted.cpu().numpy().tolist())
        results['true'].extend(labels[0].cpu().numpy().tolist())
        results['freq'].extend(labels[2].cpu().numpy().tolist())
        results['dm'].extend(labels[1].cpu().numpy().tolist())
        results['snr'].extend(labels[3].cpu().numpy().tolist())
        results['boxcar'].extend(labels[4].cpu().numpy().tolist())
        total += labels[0].size(0)
        correct_valid += (predicted.cpu() == labels[0].cpu()).sum().item()
    
    
# Calculate training accuracy after each epoch
val_accuracy = correct_valid / total * 100.0
print("===========================")
print('accuracy: ',  val_accuracy)
print("===========================")

import pickle

# Pickle the dictionary to a file
with open('models_mask/test_1.pkl', 'wb') as f:
    pickle.dump(results, f)

from sklearn.metrics import precision_score, recall_score, f1_score

# Example binary labels
true = results['true']  # ground truth
pred = results['pred']  # predicted

# Compute metrics
precision = precision_score(true, pred)
recall = recall_score(true, pred)
f1 = f1_score(true, pred)
# Get confusion matrix: TN, FP, FN, TP
tn, fp, fn, tp = confusion_matrix(true, pred).ravel()

# Compute FPR
fpr = fp / (fp + tn)

print(f"False Positive Rate: {fpr:.3f}")

print(f"Precision: {precision:.3f}")
print(f"Recall: {recall:.3f}")
print(f"F1 Score: {f1:.3f}")

2
num params encoder  50840
num params  21496282


  0%|                                                    | 0/48 [00:00<?, ?it/s]/home/pma/.conda/envs/frbnn/lib/python3.11/site-packages/torch/nn/parallel/parallel_apply.py:79: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.device(device), torch.cuda.stream(stream), autocast(enabled=autocast_enabled):
100%|███████████████████████████████████████████| 48/48 [00:43<00:00,  1.10it/s]

accuracy:  98.77
False Positive Rate: 0.018
Precision: 0.982
Recall: 0.993
F1 Score: 0.988


In [21]:
from utils import CustomDataset, transform, Convert_ONNX
from torch.utils.data import Dataset, DataLoader
from utils import CustomDataset, TestingDataset, transform
from tqdm import tqdm
import torch
import numpy as np
from resnet_model_mask import  ResidualBlock, ResNet
import torch
import torch.nn as nn
import torch.optim as optim
from tqdm import tqdm 
import torch.nn.functional as F
from torch.optim.lr_scheduler import ReduceLROnPlateau
import pickle

torch.manual_seed(1)
# torch.manual_seed(42)


device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
num_gpus = torch.cuda.device_count()
print(num_gpus)

test_data_dir = '/mnt/buf1/pma/frbnn/test_ready'
test_dataset = TestingDataset(test_data_dir, transform=transform)

num_classes = 2
testloader = DataLoader(test_dataset, batch_size=420, shuffle=True, num_workers=32)

model = ResNet(24, ResidualBlock, [3, 4, 6, 3], num_classes=num_classes).to(device)
model = nn.DataParallel(model)
model = model.to(device)
params = sum(p.numel() for p in model.parameters())
print("num params ",params)


model_1 = 'models_mask/model-26-99.13_7109.pt'
# model_1 ='models/model-47-99.125.pt'
model.load_state_dict(torch.load(model_1, weights_only=True))
model = model.eval()

# eval
val_loss = 0.0
correct_valid = 0
total = 0
results = {'output': [],'pred': [], 'true':[], 'freq':[], 'snr':[], 'dm':[], 'boxcar':[]}
model.eval()
with torch.no_grad():
    for images, labels in tqdm(testloader):
        inputs, labels = images.to(device), labels
        outputs = model(inputs, return_mask = True)
        _, predicted = torch.max(outputs, 1)
        results['output'].extend(outputs.cpu().numpy().tolist())
        results['pred'].extend(predicted.cpu().numpy().tolist())
        results['true'].extend(labels[0].cpu().numpy().tolist())
        results['freq'].extend(labels[2].cpu().numpy().tolist())
        results['dm'].extend(labels[1].cpu().numpy().tolist())
        results['snr'].extend(labels[3].cpu().numpy().tolist())
        results['boxcar'].extend(labels[4].cpu().numpy().tolist())
        total += labels[0].size(0)
        correct_valid += (predicted.cpu() == labels[0].cpu()).sum().item()
    
    
# Calculate training accuracy after each epoch
val_accuracy = correct_valid / total * 100.0
print("===========================")
print('accuracy: ',  val_accuracy)
print("===========================")

import pickle

# Pickle the dictionary to a file
with open('models_mask/test_7109.pkl', 'wb') as f:
    pickle.dump(results, f)

from sklearn.metrics import precision_score, recall_score, f1_score

# Example binary labels
true = results['true']  # ground truth
pred = results['pred']  # predicted

# Compute metrics
precision = precision_score(true, pred)
recall = recall_score(true, pred)
f1 = f1_score(true, pred)
# Get confusion matrix: TN, FP, FN, TP
tn, fp, fn, tp = confusion_matrix(true, pred).ravel()

# Compute FPR
fpr = fp / (fp + tn)

print(f"False Positive Rate: {fpr:.3f}")

print(f"Precision: {precision:.3f}")
print(f"Recall: {recall:.3f}")
print(f"F1 Score: {f1:.3f}")

2
num params encoder  50840
num params  21496282


  0%|                                                    | 0/48 [00:00<?, ?it/s]/home/pma/.conda/envs/frbnn/lib/python3.11/site-packages/torch/nn/parallel/parallel_apply.py:79: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.device(device), torch.cuda.stream(stream), autocast(enabled=autocast_enabled):
100%|███████████████████████████████████████████| 48/48 [00:44<00:00,  1.09it/s]

accuracy:  99.03
False Positive Rate: 0.009
Precision: 0.990
Recall: 0.990
F1 Score: 0.990


In [22]:
# acc
print(np.mean([99.125,98.77, 99.03 ]), np.std([99.125,98.77, 99.03 ]))
# precision
print(np.mean([0.991,0.990, 0.993]), np.std([0.991,0.990, 0.993]))
# f1
print(np.mean([0.990,0.988,0.991 ]),np.std([0.990,0.988,0.991 ]))
# fp
print(np.mean([0.008,0.018,0.009 ]),np.std([0.008,0.018,0.009]))


98.97499999999998 0.1500555452713003
0.9913333333333333 0.0012472191289246482
0.9896666666666666 0.0012472191289246482
0.011666666666666665 0.004496912521077347
